# AlexNet for Sargassum Classification Pictures by using PyTorch
Author: Javier Arellano-Verdejo  
Contact: javier.arellano@ecosur.mx & javier_arellano_verdejo@hotmail.com  
Personal webpage: http://www.ecosur.mx/ecoconsulta/personal/persona.php?id=641&nombre=Javier%20Arellano%20Verdejo  
Date: September/2020  
Version: 1.21.0208  

---

## Import libraries

In [ ]:
# for general use
import matplotlib.pyplot as plt
import numpy as np
import os, shutil
import zipfile
import itertools

# for PyTorch
import torch
import torch.nn.functional as F

from torchvision import datasets, transforms, models
from torch import nn

# for confusion matrix computing and classification report
from sklearn.metrics import confusion_matrix
from sklearn.metrics import classification_report

# for web request
from urllib.request import urlretrieve

## Get device handler

In [ ]:
device = torch.device('cuda:0' if torch.cuda.is_available() else "cpu")

# If you get an out-of-memory error on the GPU use with CPU
#device = torch.device("cpu")
print(device)


## Download the dataset and unzip it to the local folder
IMPORTANT: It is also possible to manually download the dataset from the following link:  
https://doi.org/10.6084/m9.figshare.13256174.v5

In [ ]:
# figshare URL
download_url = "https://ndownloader.figshare.com/files"

# figshare project id
project_id = "26298643"

# dataset filename
fname = "./sargassum_dataset.zip"

# path where the images will be decompressed
base_dir = '/content'

# download the dataset
try:
  urlretrieve(download_url + "/" + project_id, fname)

  # unzip the dataset
  zip_ref = zipfile.ZipFile(fname, 'r')
  zip_ref.extractall(base_dir)
  zip_ref.close()

except:
  print("The file cannot be downloaded, try manually downloading the file from " +
        "https://doi.org/10.6084/m9.figshare.13256174.v5 and unzip it to the " + 
        "directory {}".format(base_dir))


## Processes and loads the test and training dataset using augmented data

In [ ]:
transform_train = transforms.Compose([transforms.Resize((224,224)),
                                      transforms.RandomHorizontalFlip(),
                                      transforms.RandomRotation(10),
                                      transforms.RandomAffine(0, shear=10, scale=(0.8, 1.2)),
                                      transforms.ColorJitter(brightness=1.0, contrast=1.0, saturation=1.0),
                                      transforms.ToTensor(),
                                      transforms.Normalize((0.5,),(0.5,))
                                      ])

transform = transforms.Compose([transforms.Resize((224,224)),
                                transforms.ToTensor(),
                                transforms.Normalize((0.5,),(0.5,))
                                ])

training_dataset = datasets.ImageFolder(root=base_dir + '/sargassum_dataset/train', 
                                        transform=transform_train)


validation_dataset = datasets.ImageFolder(root=base_dir + '/sargassum_dataset/val', 
                                        transform=transform)


training_loader = torch.utils.data.DataLoader(dataset=training_dataset,
                                              batch_size=100,
                                              shuffle=True)

validation_loader = torch.utils.data.DataLoader(dataset=validation_dataset,
                                              batch_size=100,
                                              shuffle=False)

## Shows the size of the test and training data set as well as the classes

In [ ]:
print('Training dataset size: {}'.format(len(training_dataset)))
print('Validation dataset size: {}'.format(len(validation_dataset)))
classes = ['Without Sargassum','With Sargassum']
print('Classes: {}'.format(classes))

## Support functions

In [ ]:
# Converts a tensor into an image
def im_convert(tensor):
  image = tensor.cpu().clone().detach().numpy()
  # the tensor has the following shape [3,224,224] 
  # however for matplot to visualize it the shape 
  # must be [224,224,3]. The transpose function 
  # helps to relocate the order of the columns
  image = image.transpose(1,2,0)
  # I unnormalize the image x_new = x * std = mean 
  # in our case the mean and the std are equal to 
  # 0.5 the previous thing is because when we 
  # normalized we made the interval go from -1.0 to 1.0
  image = image * np.array((0.5, 0.5, 0.5)) + np.array((0.5, 0.5, 0.5))
  image = image.clip(0, 1)
  
  return image

# Prints the confusion matrix
def plot_confusion_matrix(cm,
                          classes,
                          normalize=False,
                          title='Confusion matrix',
                          cmap=plt.cm.Blues):
  if normalize:
    cm = cm.astype('float') / cm.sum(axis=1)[:, np.newaxis]
    print("Normalize confusion matrix")
  else:
    print("Confusion matrix, without normalization")

  print(cm)

  fig, ax = plt.subplots()
  plt.imshow(cm, interpolation='nearest', cmap=cmap)
  plt.title(title)
  plt.colorbar()
  tick_marks = np.arange(len(classes))
  plt.xticks(tick_marks, classes, rotation=45)
  plt.yticks(tick_marks, classes)

  fmt = '.2f' if normalize else 'd'
  thresh = cm.max() / 2

  for i,j in itertools.product(range(cm.shape[0]), range(cm.shape[1])):
    plt.text(j, i, format(cm[i, j], fmt),
             horizontalalignment='center',
             color='white' if cm[i,j] > thresh else 'black')
  
  plt.tight_layout()
  plt.ylabel('True label')
  plt.xlabel('Predicted label')
  plt.show()

## Show some images

In [ ]:
dataiter = iter(training_loader)
images, labels = dataiter.next()

fig = plt.figure(figsize=(25, 4))

for idx in np.arange(20):
  ax = fig.add_subplot(2, 10, idx+1)
  plt.imshow(im_convert(images[idx]))
  ax.set_title(labels[idx].item())


## Load and adapt the AlexNet model 

In [ ]:
model = models.alexnet(pretrained=True)
print(model)

## The layers we don't want to retrain are locked up

In [ ]:
for param in model.features.parameters():
  param.requires_grad = False

## The last layer is modified so that it only classifies two classes instead of 1000

In [ ]:
n_inputs = model.classifier[6].in_features
last_layer = nn.Linear(n_inputs, len(classes))
model.classifier[6] = last_layer
model.to(device)

print(model)

## The loss function and the optimizer are defined

In [ ]:
# definition of the error function. CrossEntropyLoss is the 
# best option for the classification of multiple classes
criterion = nn.CrossEntropyLoss()

# Definition of the method of optimisation
optimizer = torch.optim.Adam(model.parameters(), lr=0.0001)

## Train the Neural Network

In [ ]:
epochs = 40
running_loss_history = []
running_corrects_history = []

val_running_loss_history = []
val_running_corrects_history = []

for e in range(epochs):
  running_loss = 0.0
  running_corrects = 0.0

  val_running_loss = 0.0
  val_running_corrects = 0.0

  for inputs, labels in training_loader:
    # We use the GPU
    inputs = inputs.to(device)
    labels = labels.to(device)

    outputs = model.forward(inputs)
    loss = criterion(outputs, labels)

    optimizer.zero_grad()
    loss.backward()
    optimizer.step()

    _, pred = torch.max(outputs, 1)
    running_loss += loss.item()
    running_corrects += torch.sum(pred == labels.data)

  else:
    # saves memory by not calculating the gradient
    with torch.no_grad():
      for val_inputs, val_labels in validation_loader:
        # We use the GPU
        val_inputs = val_inputs.to(device)
        val_labels = val_labels.to(device)
        val_outputs = model.forward(val_inputs)
        val_loss = criterion(val_outputs, val_labels)      

        _, val_pred = torch.max(val_outputs, 1)
        val_running_loss += val_loss.item()
        val_running_corrects += torch.sum(val_pred == val_labels.data)

    epoch_loss = running_loss/len(training_loader.dataset)
    epoch_acc = running_corrects.float() / len(training_loader.dataset)
    running_loss_history.append(epoch_loss)
    running_corrects_history.append(epoch_acc)

    val_epoch_loss = val_running_loss/len(validation_loader.dataset)
    val_epoch_acc = val_running_corrects.float() / len(validation_loader.dataset)
    val_running_loss_history.append(val_epoch_loss)
    val_running_corrects_history.append(val_epoch_acc)

    print('Epoch: ', (e+1))
    print('Training loss: {:.4f}, acc: {:.4f} '.format(epoch_loss, epoch_acc.item()))
    print('Validation loss: {:.4f}, acc: {:.4f} '.format(val_epoch_loss, val_epoch_acc.item()))


## Feeds the Neural Network with the validation data and store the result

In [ ]:
val_running_loss = 0.0
val_running_corrects = 0.0

all_preds = torch.tensor([])
all_targets = torch.tensor([])

with torch.no_grad():
  for val_inputs, val_labels in validation_loader:
    # Usamos la GPU
    val_inputs = val_inputs.to(device)
    val_labels = val_labels.to(device)

    val_outputs = model.forward(val_inputs) 
    val_loss = criterion(val_outputs, val_labels)      

    _, val_pred = torch.max(val_outputs, 1)
    val_running_loss += val_loss.item()
    val_running_corrects += torch.sum(val_pred == val_labels.data)

    all_preds = torch.cat(
            (all_preds, val_outputs.to('cpu'))
            ,dim=0
        )
    all_targets = torch.cat(
            (all_targets, val_labels.to('cpu').type('torch.FloatTensor') )
            ,dim=0
        )

print('Validation dataset loss: {}'.format(val_running_loss))

## Displays the confusion matrix

In [ ]:
cm = confusion_matrix(all_targets, all_preds.argmax(dim=1))
plot_confusion_matrix(cm, list(range(2)))

## Prints the classification report

In [ ]:
print(classification_report(all_targets, all_preds.argmax(dim=1)))

## Plots the loss data

In [ ]:
fig, ax = plt.subplots()
plt.plot(running_loss_history, label='training loss')
plt.plot(val_running_loss_history, label='validation loss')
plt.legend()

## Plots the Neural Network Accuracy

In [ ]:
fig, ax = plt.subplots()
plt.plot(running_corrects_history, label='training accuracy')
plt.plot(val_running_corrects_history, label='validation accuracy')
plt.legend()